# **Bitcoin price forecasting - Linear Regression**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



## Global constants, dependencies, libraries and tools

In [1]:
# GDrive root
GDRIVE_DIR = "/content/drive"

# Dataset
GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"
GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_train_valid"
GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG

# Features
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"
GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"
GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"
GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

# Others
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "RandomForestRegressor"
SLOW_OPERATION = True

In [2]:
# Point Colaboratory to our Google Drive
from google.colab import drive

# Define GDrive paths
drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [3]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [4]:
# Install Spark and related dependencies
!pip install pyspark

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 2.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=d4b44655fc7d2103380e6c439eee1c1dd8fd8bbd1b093b7b4c0dec345f619025
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


## Import files

In [5]:
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"

import sys
sys.path.append(GDRIVE_UTILITIES_DIR)

from imports import *
import utilities, parameters

importlib.reload(utilities)
importlib.reload(parameters)

<module 'parameters' from '/content/drive/MyDrive/BDC/project/utilities/parameters.py'>

## Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

## Loading dataset

In [7]:
# Load datasets into pyspark dataframe objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the DataFrame
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the DataFrame
  dataset.printSchema()

In [9]:
if SLOW_OPERATION:
  dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days|
+-------------------+---+------------------+--------------+---------------

## Loading features

In [10]:
# Set the features label
FEATURES_LABEL = "features"

# Set the target variable
TARGET_VAL = 'market-price'

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-20-days', 'sma-50-days', 'n-unique-addresses', 'difficulty', 'hash-rate', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


## Evaluate simple model

In [14]:
# Get default params
params = parameters.get_defaults_model_params(MODEL_NAME)
params

{'numTrees': [20], 'maxDepth': [5]}

In [15]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_all

Model    Type      Features Parameters         RMSE  \
0  RandomForestRegressor  simple  all_features    [20, 5]  4933.648021   

       MAPE         MAE      Variance        R2  Adjusted_R2       Time  
0  0.150334  3912.20714  1.501239e+08  0.868295     0.868264  14.090808

In [16]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [17]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_more_rel

Model    Type           Features Parameters         RMSE  \
0  RandomForestRegressor  simple  more_rel_features    [20, 5]  5099.735851   

       MAPE          MAE      Variance        R2  Adjusted_R2      Time  
0  0.170328  4328.762786  2.253922e+08  0.859278     0.859245  5.795348

In [18]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [19]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_less_rel

Model    Type           Features Parameters          RMSE  \
0  RandomForestRegressor  simple  less_rel_features    [20, 5]  18968.642802   

       MAPE           MAE      Variance        R2  Adjusted_R2      Time  
0  0.741978  16779.309303  1.917006e+08 -0.946876    -0.947336  5.118375

In [20]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Hyperparameter tuning

In [21]:
choosen_features = more_rel_features
CHOSEN_FEATURES_LABEL = GDRIVE_MORE_REL_FEATURES_NAME

In [22]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [23]:
# Get simple params
params = parameters.get_model_params(MODEL_NAME)
params

{'numTrees': [5, 10, 15, 20, 25], 'maxDepth': [2, 3, 5, 7, 10]}

In [24]:
hyp_res, hyp_params = utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type           Features  Proportion  \
0  RandomForestRegressor  autotuning  more_rel_features         0.9   

  Parameters         RMSE      MAPE          MAE      Variance        R2  \
0    [5, 10]  1395.640229  0.056809  1103.032922  1.512647e+07  0.787209   

   Adjusted_R2      Time  
0     0.787109  3.292201

## Cross validation

In [25]:
# Get tuned params
params = hyp_params
params

{'numTrees': [5], 'maxDepth': [10]}

In [26]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [27]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type           Features  Splits Train&Validation  \
0  RandomForestRegressor  mulTs  more_rel_features       1   (21182, 21181)   
1  RandomForestRegressor  mulTs  more_rel_features       2   (42363, 21181)   
2  RandomForestRegressor  mulTs  more_rel_features       3   (63544, 21181)   
3  RandomForestRegressor  mulTs  more_rel_features       4   (84725, 21181)   
4  RandomForestRegressor  mulTs  more_rel_features       5  (105906, 21181)   

  Parameters          RMSE      MAPE           MAE      Variance        R2  \
0    [5, 10]   6658.598973  0.664365   5155.416432  2.657188e+07 -1.485708   
1    [5, 10]   1117.148977  0.177492    933.187308  6.699258e+06  0.764464   
2    [5, 10]   1329.608471  0.130504   1215.173185  3.323576e+06  0.303413   
3    [5, 10]  33426.583484  0.664345  30706.596918  9.435663e+08 -5.308612   
4    [5, 10]   4429.372539  0.139742   3270.325879  1.122959e+08  0.763751   

   Adjusted_R2      Time  
0    -1.486413  2.390130  
1     0.764397  4.595692  
2     0.303216  3.372883  
3    -5.310400  4.323997  
4     0.763684  4.136455

In [28]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type           Features  Splits Train&Validation  \
0  RandomForestRegressor  blkTs  more_rel_features       1    (10166, 2542)   
1  RandomForestRegressor  blkTs  more_rel_features       2    (10166, 2542)   
2  RandomForestRegressor  blkTs  more_rel_features       3    (10166, 2542)   
3  RandomForestRegressor  blkTs  more_rel_features       4    (10166, 2542)   
4  RandomForestRegressor  blkTs  more_rel_features       5    (10166, 2542)   
5  RandomForestRegressor  blkTs  more_rel_features       6    (10166, 2542)   
6  RandomForestRegressor  blkTs  more_rel_features       7    (10166, 2542)   
7  RandomForestRegressor  blkTs  more_rel_features       8    (10166, 2542)   
8  RandomForestRegressor  blkTs  more_rel_features       9    (10166, 2542)   
9  RandomForestRegressor  blkTs  more_rel_features      10    (10166, 2542)   

  Parameters          RMSE      MAPE          MAE      Variance        R2  \
0    [5, 10]     30.122319  0.043232    25.675651  1.019371e+03 -1.464224   
1    [5, 10]    879.372375  0.319443   714.399758  5.105979e+05 -1.860248   
2    [5, 10]   1265.246244  0.113094  1105.078016  4.973714e+06  0.355573   
3    [5, 10]    575.835441  0.057116   285.635355  8.262795e+04  0.118346   
4    [5, 10]   1594.439165  0.125907  1411.738518  2.249258e+06 -2.785654   
5    [5, 10]    710.482814  0.089236   602.000402  1.017140e+06  0.456636   
6    [5, 10]  12080.609745  0.305109  9919.750812  9.847557e+07 -1.997570   
7    [5, 10]   1730.667233  0.028790  1413.169743  3.141509e+07  0.897666   
8    [5, 10]   6848.782521  0.255007  5428.950308  3.007205e+07 -1.203754   
9    [5, 10]   2016.807193  0.057878  1503.853790  3.834576e+06  0.281608   

   Adjusted_R2      Time  
0    -1.470056  2.000338  
1    -1.867018  2.617431  
2     0.354048  2.641699  
3     0.116259  2.384962  
4    -2.794615  1.996930  
5     0.455350  2.815826  
6    -2.004665  2.914258  
7     0.897424  2.123110  
8    -1.208970  1.927534  
9     0.279908  2.758152

## Comparison table

In [29]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [30]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model        Type           Features Parameters  \
0  RandomForestRegressor      simple       all_features    [20, 5]   
0  RandomForestRegressor      simple  more_rel_features    [20, 5]   
0  RandomForestRegressor      simple  less_rel_features    [20, 5]   
0  RandomForestRegressor  autotuning  more_rel_features    [5, 10]   
0  RandomForestRegressor       mulTs  more_rel_features    [5, 10]   
0  RandomForestRegressor       blkTs  more_rel_features    [5, 10]   

           RMSE      MAPE           MAE      Variance        R2  Adjusted_R2  \
0   4933.648021  0.150334   3912.207140  1.501239e+08  0.868295     0.868264   
0   5099.735851  0.170328   4328.762786  2.253922e+08  0.859278     0.859245   
0  18968.642802  0.741978  16779.309303  1.917006e+08 -0.946876    -0.947336   
0   1395.640229  0.056809   1103.032922  1.512647e+07  0.787209     0.787109   
0   9392.262489  0.355290   8256.139944  2.184914e+08 -0.992538    -0.993103   
0   2773.236505  0.139481   2241.025235  1.726316e+07 -0.720162    -0.724233   

        Time  
0  14.090808  
0   5.795348  
0   5.118375  
0   3.292201  
0   3.763831  
0   2.418024

## Training the final model

In [31]:
model = utilities.train_final_model(df, more_rel_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [32]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [33]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)